In [1]:
import pandas as pd
import lightgbm as lgb
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from imblearn.over_sampling import SMOTE
from sklearn.metrics import accuracy_score, classification_report
import optuna

/Users/harishsundaralingam/myworkspace/sentiment_analysis/venv/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
df = pd.read_csv('/Users/harishsundaralingam/myworkspace/sentiment_analysis/model_notebooks/dataset.csv').dropna(subset=['clean_comment'])
df.shape

(36662, 2)

In [3]:
import mlflow
# Step 2: Set up the MLflow tracking server
mlflow.set_tracking_uri("http://127.0.0.1:5000")

In [4]:
# Set or create an experiment
mlflow.set_experiment("LightGBM")

<Experiment: artifact_location='mlflow-artifacts:/370992354331275290', creation_time=1755040775773, experiment_id='370992354331275290', last_update_time=1755040775773, lifecycle_stage='active', name='LightGBM', tags={}>

In [5]:
df['category'] = df['category'].map({-1: 2, 0: 0, 1: 1})

In [6]:
df = df.dropna(subset=['category'])

In [7]:
ngram_range = (1, 3)  # Trigram setting
max_features = 1000  # Set max_features to 1000 for TF-IDF

In [8]:
# Step 4: Train-test split before vectorization and resampling
X_train, X_test, y_train, y_test = train_test_split(df['clean_comment'], df['category'], test_size=0.2, random_state=42, stratify=df['category'])

In [9]:
# Step 2: Vectorization using TF-IDF, fit on training data only
vectorizer = TfidfVectorizer(ngram_range=ngram_range, max_features=max_features)
X_train_vec = vectorizer.fit_transform(X_train)  # Fit on training data
X_test_vec = vectorizer.transform(X_test)  # Transform test data

In [10]:
X_train_vec.shape

(29329, 1000)

In [11]:
smote = SMOTE(random_state=42)
X_train_vec, y_train = smote.fit_resample(X_train_vec, y_train)

In [12]:
def log_mlflow(model_name, model, X_train, X_test, y_train, y_test):
    with mlflow.start_run():
        # Log model type
        mlflow.set_tag("mlflow.runName", f"{model_name}_SMOTE_TFIDF_Trigrams")
        mlflow.set_tag("experiment_type", "algorithm_comparison")

        # Log algorithm name as a parameter
        mlflow.log_param("algo_name", model_name)

        # Train model
        model.fit(X_train, y_train)
        y_pred = model.predict(X_test)

        # Log accuracy
        accuracy = accuracy_score(y_test, y_pred)
        mlflow.log_metric("accuracy", accuracy)

        # Log classification report
        classification_rep = classification_report(y_test, y_pred, output_dict=True)
        for label, metrics in classification_rep.items():
            if isinstance(metrics, dict):
                for metric, value in metrics.items():
                    mlflow.log_metric(f"{label}_{metric}", value)

        # Log the model
        mlflow.sklearn.log_model(model, f"{model_name}_model")

In [13]:
def objective(trial):
    params = {
        'objective': 'multiclass',
        'num_class': 3,  # Adjust based on your number of classes
        'boosting_type': trial.suggest_categorical("boosting_type", ["gbdt", "dart"]),
        'max_depth': trial.suggest_int('max_depth', 3, 12),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'n_estimators': trial.suggest_int('n_estimators', 100, 1000),
        'subsample': trial.suggest_float('subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
        'random_state': 42
    }
    
    model = lgb.LGBMClassifier(**params, silent=True)
    model.fit(
        X_train_vec, y_train
    )
    preds = model.predict(X_test_vec)
    accuracy = accuracy_score(y_test, preds)
    
    # Return negative accuracy since Optuna minimizes
    return -accuracy

In [14]:
study = optuna.create_study(direction='minimize')  # or 'maximize' for accuracy
study.optimize(objective, n_trials=30)  # Adjust n_trials as needed

# Print results
print("Best trial:")
print(f"Value: {study.best_trial.value}")
print("Params:")
for key, value in study.best_trial.params.items():
    print(f"  {key}: {value}")

[I 2025-08-12 21:43:37,277] A new study created in memory with name: no-name-8e5f7c46-8eac-4ce2-bfec-8f6d34147bb0


[LightGBM] [Warning] Unknown parameter: silent
[LightGBM] [Warning] Unknown parameter: silent
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.072672 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 99541
[LightGBM] [Info] Number of data points in the train set: 37848, number of used features: 975
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Wa

/Users/harishsundaralingam/myworkspace/sentiment_analysis/venv/lib/python3.12/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
[I 2025-08-12 21:44:34,797] Trial 0 finished with value: -0.7899904541115506 and parameters: {'boosting_type': 'dart', 'max_depth': 12, 'learning_rate': 0.19859955146997194, 'n_estimators': 553, 'subsample': 0.7926767872001808, 'colsample_bytree': 0.7003827483850398}. Best is trial 0 with value: -0.7899904541115506.


[LightGBM] [Warning] Unknown parameter: silent
[LightGBM] [Warning] Unknown parameter: silent
[LightGBM] [Warning] Unknown parameter: silent
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.091471 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 99541
[LightGBM] [Info] Number of data points in the train set: 37848, number of used features: 975
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further

/Users/harishsundaralingam/myworkspace/sentiment_analysis/venv/lib/python3.12/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
[I 2025-08-12 21:44:41,549] Trial 1 finished with value: -0.7905359334515205 and parameters: {'boosting_type': 'gbdt', 'max_depth': 3, 'learning_rate': 0.13778444976134646, 'n_estimators': 899, 'subsample': 0.7511174834483489, 'colsample_bytree': 0.9597157720006293}. Best is trial 1 with value: -0.7905359334515205.


...

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Unknown parameter: silent
[LightGBM] [Warning] Unknown parameter: silent
[LightGBM] [Warning] Unknown parameter: silent
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.072898 seconds.
You c

/Users/harishsundaralingam/myworkspace/sentiment_analysis/venv/lib/python3.12/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(


[LightGBM] [Warning] Unknown parameter: silent


[I 2025-08-12 21:54:46,249] Trial 29 finished with value: -0.787399427246693 and parameters: {'boosting_type': 'dart', 'max_depth': 6, 'learning_rate': 0.19983782643340486, 'n_estimators': 949, 'subsample': 0.6669866457279368, 'colsample_bytree': 0.6280099010509805}. Best is trial 21 with value: -0.7916268921314605.


Best trial:
Value: -0.7916268921314605
Params:
  boosting_type: gbdt
  max_depth: 4
  learning_rate: 0.11307765486202531
  n_estimators: 890
  subsample: 0.5774192166207097
  colsample_bytree: 0.5032023417736593


In [15]:
study.best_params

{'boosting_type': 'gbdt',
 'max_depth': 4,
 'learning_rate': 0.11307765486202531,
 'n_estimators': 890,
 'subsample': 0.5774192166207097,
 'colsample_bytree': 0.5032023417736593}

In [16]:
best_params = study.best_params
best_model = lgb.LGBMClassifier(**best_params)

# Log the best model with MLflow, passing the algo_name as "xgboost"
log_mlflow("LightGBM", best_model, X_train_vec, X_test_vec, y_train, y_test)

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.070710 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 99541
[LightGBM] [Info] Number of data points in the train set: 37848, number of used features: 975
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further s

/Users/harishsundaralingam/myworkspace/sentiment_analysis/venv/lib/python3.12/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
2025/08/12 21:55:04 WARNING mlflow.models.model: `artifact_path` is deprecated. Please use `name` instead.
2025/08/12 21:55:07 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.


🏃 View run LightGBM_SMOTE_TFIDF_Trigrams at: http://127.0.0.1:5000/#/experiments/370992354331275290/runs/40d56a904f73450581da34df68289a83
🧪 View experiment at: http://127.0.0.1:5000/#/experiments/370992354331275290
